<a href="https://colab.research.google.com/github/morteza/notebooks/blob/master/xicorr.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [1]:
import numpy as np

import seaborn as sns; sns.set()

In [8]:

def xicorr(X,Y):
    n = X.size
    xi = np.argsort(X,kind='quicksort')
    Y = Y[xi]
    _,b,c = np.unique(Y,return_counts=True,return_inverse=True)
    r = np.cumsum(c)[b]
    _,b,c = np.unique(-Y,return_counts=True,return_inverse=True)
    l = np.cumsum(c)[b]
    return 1 - n*np.abs(np.diff(r)).sum() / (2*(l*(n-l)).sum())


def xicorr2(x: 'ArrayLike', y: 'ArrayLike') -> float:
    """xi correlation coefficient (alternative implementation)

    Written by github/atarashansky, modified by github/escherba
    https://github.com/czbiohub/xicor/issues/17#issue-965635013
    """
    x = np.asarray(x)
    y = np.asarray(y)
    n = x.size
    assert y.size == n, "arrays must be of the same size"
    y = y[np.argsort(x, kind='quicksort')]
    _, inverse, counts = np.unique(y, return_inverse=True, return_counts=True)
    right = np.cumsum(counts)[inverse]
    left = np.cumsum(np.flip(counts))[(counts.size - 1) - inverse]
    return 1. - 0.5 * float(np.abs(np.diff(right)).sum() / np.mean(left * (n - left)))

from scipy.stats import rankdata

def xicorr_orig(x: 'ArrayLike', y: 'ArrayLike') -> float:
    """Original R implementation of Xi translated into Python

    R implementation:
    https://github.com/cran/XICOR/blob/master/R/calculateXI.R
    """
    x = np.asarray(x)
    y = np.asarray(y)
    n = x.size
    assert y.size == n, "arrays must be of the same size"
    PI = rankdata(x, method="average")
    fr = rankdata(y, method="average")
    CU = np.mean((float(n + 1) - fr) * (fr - 1.))
    A1 = np.abs(np.diff(fr[np.argsort(PI, kind="quicksort")])).sum()
    return 1. - 0.5 * float(A1 / CU)

In [84]:
x = np.random.rand(125) + 2
y = x**2 + x + np.sqrt(x) + 12 + np.random.randn(125)

from scipy.stats import pearsonr

xicorr(x, y), xicorr2(x, y), xicorr_orig(x, y), pearsonr(x, y)[0]

(0.5468509984639016,
 0.5468509984639016,
 0.5468509984639016,
 0.8923135014900104)